###  dataset https://www.consumerfinance.gov/data-research/
https://www.consumerfinance.gov/data-research/consumer-complaints/

What the consumers were complaining in the financial product and service market? 
Data from these complaints help us understand the financial marketplace and protect consumers.

In [0]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import stats
import seaborn as sns

#### Data acquisition
- download [json format datasource](http://files.consumerfinance.gov/ccdb/complaints.json.zip) to local and unzip
- upload unzipped json file to DBFS
- read json file and partion by 
- create dellta table. Delta Engine is a high performance, Apache Spark compatible query engine that provides an efficient way to process data in data lakes including data stored in open source Delta Lake. Delta Engine optimizations accelerate data lake operations, supporting a variety of workloads ranging from large-scale ETL processing to ad-hoc, interactive queries.

In [0]:
#make sure file uploaded 6s
#dbutils.fs.rm('dbfs:/FileStore/tables/complaints_csv.zip',True)
#dbutils.fs.rm('dbfs:/FileStore/tables/complaints_json.zip',True)
#dbutils.fs.rm('dbfs:/FileStore/tables/complaints-1.json',True)
display(dbutils.fs.ls("dbfs:/FileStore/tables/"))

path name size dbfs:/FileStore/tables/complaints.csv complaints.csv 1233411049 dbfs:/FileStore/tables/complaints.json complaints.json 1942366519 dbfs:/FileStore/tables/exercise_pyspark_dataframe.ipynb exercise_pyspark_dataframe.ipynb 30542 dbfs:/FileStore/tables/flight_model/ flight_model/ 0 dbfs:/FileStore/tables/flight_weather.csv flight_weather.csv 431664555

In [0]:
file_name = '/FileStore/tables/complaints.json'
#for line,item in zip(open(file_name,'r').readlines(), range(3)):
#    print(line)
   
df = spark.read.format('json').load(file_name)
df.dtypes

Out[53]: [('_corrupt_record', 'string'),
 ('company', 'string'),
 ('company_public_response', 'string'),
 ('company_response', 'string'),
 ('complaint_id', 'string'),
 ('complaint_what_happened', 'string'),
 ('consumer_consent_provided', 'string'),
 ('consumer_disputed', 'string'),
 ('date_received', 'string'),
 ('date_sent_to_company', 'string'),
 ('issue', 'string'),
 ('product', 'string'),
 ('state', 'string'),
 ('sub_issue', 'string'),
 ('sub_product', 'string'),
 ('submitted_via', 'string'),
 ('tags', 'string'),
 ('timely', 'string'),
 ('zip_code', 'string')]

#### Data cleansing
- Check date range, remove the top and bottom half month data (such as 2021/02)
- Delete data withought primary key (Complaint ID)

In [0]:
df.show(n=3, truncate=False, vertical=True)

-RECORD 0-----------------------------------------------------------------------------------------------------------------------
 _corrupt_record | [ 
 company | null 
 company_public_response | null 
 company_response | null 
 complaint_id | null 
 complaint_what_happened | null 
 consumer_consent_provided | null 
 consumer_disputed | null 
 date_received | null 
 date_sent_to_company | null 
 issue | null 
 product | null 
 state | null 
 sub_issue | null 
 sub_product | null 
 submitted_via | null 
 tags | null 
 timely | null 
 zip_code | null 
-RECORD 1-----------------------------------------------------------------------------------------------------------------------
 _corrupt_record | null 
 company | TRANSWORLD SYSTEMS INC 
 company_public_response | 
 company_response | Closed with explanation 
 complaint_id | 3384392 
 complaint_what_happened | transworld systems inc. 
is trying to collect a debt that is not mine, not owed and is inaccurate. 
 consumer_consent_provided | Consent provided 
 consumer_disputed | N/A 
 date_received | 2019-09-24 
 date_sent_to_company | 2019-09-24 
 issue | Attempts to collect debt not owed 
 product | Debt collection 
 state | FL 
 sub_issue | Debt is not yours 
 sub_product | I do not know 
 submitted_via | Web 
 tags | 
 timely | Yes 
 zip_code | 335XX 
-RECORD 2-----------------------------------------------------------------------------------------------------------------------
 _corrupt_record | null 
 company | Experian Information Solutions Inc. 
 company_public_response | Company has responded to the consumer and the CFPB and chooses not to provide a public response 
 company_response | Closed with non-monetary relief 
 complaint_id | 3379500 
 complaint_what_happened | 
 consumer_consent_provided | Consent not provided 
 consumer_disputed | N/A 
 date_received | 2019-09-19 
 date_sent_to_company | 2019-09-20 
 issue | Incorrect information on your report 
 product | Credit reporting, credit repair services, or other personal consumer reports 
 state | PA 
 sub_issue | Information belongs to someone else 
 sub_product | Credit reporting 
 submitted_via | Web 
 tags | 
 timely | Yes 
 zip_code | 15206 
only showing top 3 rows

In [0]:
count = df.count()

In [0]:
#https://blog.csdn.net/sinat_26917383/article/details/80500349
from pyspark.sql.functions import isnull
# delete null rows of these columns
df = df.dropna(subset=['complaint_id', 'issue','product','date_received','company','state','submitted_via'])

In [0]:
#rows deleted
print (count - df.count())

2

In [0]:
df.createOrReplaceTempView('t_complaints')

#### Time related questions

- What's the average processing time of the closed complaints. We don't know because lack of close time recorded.
- Are they resolved timely? 
- Are the consumers satisfied?

Let's see **timely** column. It shows **98%** of these complaints are timely resolved.

In [0]:
# what's the values in timely column
display(df.select(['timely']).groupby('timely').count())

timely count No 39765 Yes 1920683

- Which company has the highest delay rate? 
- How these delaid record distributes?
######Let's check companies with over 100 complaints and have delay process.

In [0]:
# how these intimely data dristributed in these financial companies 
df_delay = sqlContext.sql("SELECT company,sum(IF(timely='No', 1, 0)) AS delay_count, count(1) as total " + \
                           " FROM t_complaints " +\
                           " GROUP BY company " + 
                           " HAVING sum(IF(timely='No', 1, 0))>0 and count(1)>100")
pddf_delay = df_delay.toPandas()

In [0]:
#calculate delay rate
pddf_delay['percent'] = pddf_delay.apply(lambda x: float(("%.2f")%((x['delay_count'] / x['total'])*100)), axis=1)  
#keep those delay rate over 80%
pddf_delay_percent = pddf_delay[pddf_delay['percent'] > 80].sort_values("percent", ascending=False)

In [0]:
 display(pddf_delay.sort_values("total", ascending=False))

company delay_count total percent EQUIFAX, INC. 1687 232551 0.73 TRANSUNION INTERMEDIATE HOLDINGS, INC. 96 224589 0.04 Experian Information Solutions Inc. 9 222666 0.0 BANK OF AMERICA, NATIONAL ASSOCIATION 1631 97852 1.67 WELLS FARGO & COMPANY 3807 83815 4.54 JPMORGAN CHASE & CO. 96 75470 0.13 CITIBANK, N.A. 367 63120 0.58 CAPITAL ONE FINANCIAL CORPORATION 71 50644 0.14 Navient Solutions, LLC. 3 33770 0.01 Ocwen Financial Corporation 545 30725 1.77 SYNCHRONY FINANCIAL 17 30205 0.06 U.S. BANCORP 92 23394 0.39 NATIONSTAR MORTGAGE 130 23161 0.56 AMERICAN EXPRESS COMPANY 4 18979 0.02 PNC Bank N.A. 110 16993 0.65 PORTFOLIO RECOVERY ASSOCIATES INC 2 15227 0.01 Ditech Financial LLC 42 14953 0.28 ENCORE CAPITAL GROUP INC. 25 14613 0.17 DISCOVER BANK 15 14598 0.1 TD BANK US HOLDING COMPANY 9 13651 0.07 AES/PHEAA 7 11699 0.06 Alliance Data Card Services 2 10753 0.02 SELECT PORTFOLIO SERVICING, INC. 61 10319 0.59 HSBC NORTH AMERICA HOLDINGS INC. 158 9976 1.58 SUNTRUST BANKS, INC. 6 9643 0.06 BARCLAYS BANK DELAWARE 5 9583 0.05 Paypal Holdings, Inc 19 9116 0.21 ERC 31 9034 0.34 Santander Consumer USA Holdings Inc. 5 8528 0.06 UNITED SERVICES AUTOMOBILE ASSOCIATION 71 8161 0.87 ALLY FINANCIAL INC. 1 8072 0.01 CITIZENS FINANCIAL GROUP, INC. 3 7576 0.04 Resurgent Capital Services L.P. 13 7291 0.18 NAVY FEDERAL CREDIT UNION 10 7076 0.14 FIFTH THIRD FINANCIAL CORPORATION 20 7036 0.28 TRANSWORLD SYSTEMS INC 4 6093 0.07 Specialized Loan Servicing Holdings LLC 67 6073 1.1 Convergent Resources, Inc. 6 5926 0.1 BB&T CORPORATION 16 5524 0.29 Shellpoint Partners, LLC 65 5198 1.25 M&T BANK CORPORATION 43 5158 0.83 REGIONS FINANCIAL CORPORATION 109 4974 2.19 I.C. System, Inc. 3 4945 0.06 Diversified Consultants, Inc. 25 4939 0.51 Nelnet, Inc. 36 4775 0.75 Seterus, Inc. 13 4488 0.29 BBVA FINANCIAL CORPORATION 2 4305 0.05 KEYCORP 20 4293 0.47 LoanCare, LLC 32 4076 0.79 Caliber Home Loans, Inc. 26 3860 0.67 SANTANDER BANK, NATIONAL ASSOCIATION 78 3697 2.11 Comerica 21 3655 0.57 CARRINGTON MORTGAGE SERVICES, LLC 27 3616 0.75 Freedom Mortgage Company 25 3578 0.7 LEXISNEXIS 13 3526 0.37 BAYVIEW LOAN SERVICING, LLC 52 3524 1.48 National Credit Systems,Inc. 165 3410 4.84 Coinbase, Inc. 6 3384 0.18 CCS Financial Services, Inc. 93 3316 2.8 CL Holdings LLC 5 3300 0.15 Commonwealth Financial Systems, Inc. 27 3144 0.86 WESTERN UNION COMPANY, THE 31 3036 1.02 General Motors Financial Company, Inc. 9 3024 0.3 HUNTINGTON NATIONAL BANK, THE 4 3016 0.13 QUICKEN LOANS, INC. 34 2926 1.16 Fidelity National Information Services, Inc. (FNIS) 13 2882 0.45 RUSHMORE LOAN MANAGEMENT SERVICES LLC 17 2652 0.64 ONEMAIN FINANCIAL HOLDINGS, LLC. 5 2646 0.19 TOYOTA MOTOR CREDIT CORPORATION 1 2558 0.04 Southwest Credit Systems, L.P. 304 2546 11.94 PENNYMAC LOAN SERVICES, LLC. 13 2468 0.53 PHH Mortgage Services Corporation 16 2450 0.65 HW Holding, Inc 56 2446 2.29 TCF NATIONAL BANK 52 2310 2.25 HCFS Health Care Financial Services, Inc. 88 2273 3.87 SLM CORPORATION 2 2265 0.09 MONEYGRAM PAYMENT SYSTEMS WORLDWIDE INC 9 2188 0.41 EOS Holdings, Inc. 16 2187 0.73 CREDIT ACCEPTANCE CORPORATION 1 2136 0.05 CIT BANK, NATIONAL ASSOCIATION 117 2116 5.53 NETSPEND CORPORATION 11 2056 0.54 HYUNDAI CAPITAL AMERICA 52 2028 2.56 ENOVA INTERNATIONAL, INC. 5 1970 0.25 BMO HARRIS BANK NATIONAL ASSOCIATION 9 1964 0.46 Square Inc. 30 1962 1.53 Midwest Recovery Systems 306 1922 15.92 CORELOGIC INC 13 1899 0.68 PENTAGON FEDERAL CREDIT UNION 8 1874 0.43 Receivables Performance Management, LLC 77 1858 4.14 EXPERT GLOBAL SOLUTIONS, INC. 3 1821 0.16 CURO Intermediate Holdings 2 1820 0.11 NISSAN MOTOR ACCEPTANCE CORPORATION 9 1805 0.5 National Credit Adjusters, LLC 116 1805 6.43 Westlake Services, LLC 33 1783 1.85 TRUIST FINANCIAL CORPORATION 4 1772 0.23 AMERICAN HONDA FINANCE CORP 8 1756 0.46 Fay Servicing, LLC 81 1712 4.73 BANK OF THE WEST 72 1706 4.22 Selene Finance LP 16 1695 0.94 Allied Interstate LLC 4 1647 0.24 Populus Financial Group, Inc. 34 1621 2.1 FIRST NATIONAL BANK OF OMAHA 19 1581 1.2 Credence Resour

- These companies have highest delay rate. Let's see their information. The complaints records are hundred level. As this dataset is from 2015 by now. Checking it's distribution.

In [0]:
display(pddf_delay_percent)

company delay_count total percent Mobiloans, LLC 451 451 100.0 Ameritech Financial 197 217 90.78 Credit Collections U.S.A., L.L.C. 113 130 86.92 High Point Asset Inc 122 141 86.52

#### What are the most complained products?
- Credit report related (), Debt collection, Credit card related(), morgage, student loan.
- **Credit reporting, credit repair services, or other personal consumer reports** has the highest complaints. Checking sub-product to see what happened.

In [0]:
df_service = sqlContext.sql("SELECT product,count(1) AS count " + \
                           " FROM t_complaints " +\
                           " GROUP BY product ORDER BY 2")
display(df_service)

product count Virtual currency 18 Other financial service 1059 Prepaid card 3819 Money transfers 5354 Payday loan 5543 Payday loan, title loan, or personal loan 16071 Vehicle loan or lease 22572 Money transfer, virtual currency, or money service 22682 Consumer Loan 31604 Student loan 60527 Checking or savings account 81865 Bank account or service 86206 Credit card 89190 Credit card or prepaid card 101676 Credit reporting 140432 Mortgage 319712 Debt collection 334064 Credit reporting, credit repair services, or other personal consumer reports 638054

**Credit reporting, credit repair services, or other personal consumer reports** has the highest complaints. Checking sub-product to see what happened.
- Over 99% of these complaints are about **Credit reporting**

In [0]:
df_subproduct = sqlContext.sql("SELECT sub_product,count(1) AS count " + \
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " GROUP BY sub_product ORDER BY 2")
display(df_subproduct)

sub_product count Conventional home mortgage 1 Credit repair services 1700 Other personal consumer report 6468 Credit reporting 629885

##### What's the issues about **Credit reporting**?
- Check the issue and sub issues, the most complaints focus on **the consumer received Incorrect information on the report in which the Information belongs to someone else**. Ti's about the quality of information service.
- Is this kind of problem very commonly distributed in financial companies?

In [0]:
df_issue = sqlContext.sql("SELECT issue,sub_issue,count(issue) AS count_issue,count(sub_issue) as count_sub_issue " + \
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " AND sub_product='Credit reporting' " +\
                           " GROUP BY issue,sub_issue")
display(df_issue)

issue sub_issue count_issue count_sub_issue Credit monitoring or identity theft protection services Problem canceling credit monitoring or identify theft protection service 999 999 Incorrect information on your report Account information incorrect 46398 46398 Credit monitoring or identity theft protection services Received unwanted marketing or advertising 249 249 Problem with a credit reporting company's investigation into an existing problem Their investigation did not fix an error on your report 85923 85923 Problem with fraud alerts or security freezes 9822 9822 Credit monitoring or identity theft protection services Didn't receive services that were advertised 757 757 Problem with a credit reporting company's investigation into an existing problem Problem with personal statement of dispute 5561 5561 Incorrect information on your report Information belongs to someone else 256333 256333 Improper use of your report Received unsolicited financial product or insurance offers after opting out 397 397 Getting a loan or lease Credit denial 3 3 Problem with a credit reporting company's investigation into an existing problem Difficulty submitting a dispute or getting information about a dispute over the phone 8369 8369 Improper use of your report Report provided to employer without your written authorization 357 357 Problem with a credit reporting company's investigation into an existing problem Investigation took more than 30 days 25842 25842 Unable to get your credit report or credit score Problem getting your free annual credit report 4922 4922 Incorrect information on your report Information is missing that should be on the report 6404 6404 Dealing with your lender or servicer Received bad information about your loan 1 1 Credit monitoring or identity theft protection services Problem with product or service terms changing 668 668 Improper use of your report Credit inquiries on your report that you don't recognize 37816 37816 Getting the loan 1 1 Problem with the payoff process at the end of the loan 1 1 Problem when making payments Problem during payment process 1 1 Getting a credit card Card opened as result of identity theft or fraud 1 1 Incorrect information on your report Personal information incorrect 21203 21203 Credit monitoring or identity theft protection services Billing dispute for services 2018 2018 Improper use of your report Reporting company used your report improperly 17640 17640 Unable to get your credit report or credit score Other problem getting your report or credit score 5793 5793 Problem with a credit reporting company's investigation into an existing problem Was not notified of investigation status or results 20928 20928 Incorrect information on your report Public record information inaccurate 10384 10384 Incorrect information on your report Account status incorrect 49916 49916 Closing on a mortgage 2 2 Incorrect information on your report Old information reappears or never goes away 11174 11174 Incorrect information on your report 2 2

##### Which company contributed this issue most?
- Check how this issue distributed in within these companies. Have they dealed these complaints timely?
TRANSUNION INTERMEDIATE HOLDINGS, INC. , Experian Information Solutions Inc. and EQUIFAX, INC. have the highest count of complaints on this issue. By google these companies, we can find these are established for over 30 years financial company. Is this because they have a big consumer group?

In [0]:
df_company_issue = sqlContext.sql("SELECT company,count(1) as count, " + \
                           " round((sum(IF(timely='No', 1, 0))/count(1))*100,2) as delay_percent " +\
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " AND sub_product='Credit reporting' " +\
                           " AND issue='Incorrect information on your report' AND sub_issue='Information belongs to someone else' "\
                           " GROUP BY company")
display(df_company_issue)

company count delay_percent PlusFour, Inc 6 0.0 FORD MOTOR CREDIT CO. 38 0.0 ClearOne Advantage, LLC 2 0.0 GLOBAL PAYMENTS DIRECT INC. 3 0.0 International Collection Systems, Inc. 1 0.0 Manhattan Beach Venture, LLC 1 100.0 Medical Data Systems, Inc. 26 0.0 Southern Credit Recovery, Inc. 5 0.0 Nelson Cruz & Associates LLC 8 75.0 AFNI INC. 95 0.0 MLH Financial Services, Inc. 2 100.0 Atlas Credit Company, Inc. 2 0.0 Receivable Solutions, Inc. 5 0.0 Credit Solutions, LLC (KY) 1 0.0 Account Resolution Corporation 2 0.0 World Omni Financial Corp. 10 0.0 Fidelity National Information Services, Inc. (FNIS) 354 0.0 ULRS, Inc. 1 0.0 MUFG AMERICAS HOLDINGS CORPORATION 1 0.0 OpenRoad Lending 6 0.0 Collection Service Center, Inc. 2 0.0 Automated Accounts, Inc. 2 0.0 Receivables Management Partners, LLC 11 0.0 TRIDENT MORTGAGE COMPANY, LP 1 0.0 Selene Holdings LLC 1 0.0 BROKER SOLUTIONS, INC. 1 0.0 AUTOMOBILE ACCEPTANCE CORPORATION 4 0.0 PMR Progressive, LLC 1 100.0 Clarity Services 70 14.29 SOUTHWEST COLLECTION SERVICES INC. 3 0.0 ATG Credit, LLC 6 0.0 Capital Accounts, LLC 20 20.0 Second Round Limited Partnership, Austin, TX Branch 2 0.0 Merchants Acceptance Corp 3 0.0 Grant Mercantile Agency 5 0.0 RockLoans Holdings LLC 1 0.0 Automotive Management Services, Inc. 2 100.0 BOEING EMPLOYEES CREDIT UNION 9 0.0 National Recovery Service, Inc. 1 100.0 GOLDMAN SACHS BANK USA 29 0.0 INDUSTRIAL AND COMMERCIAL BANK OF CHINA (USA), NATIONAL ASSOCIATION 1 0.0 R.C. Temme Corporation 1 0.0 Concentric Receivables Management, Ltd. 1 0.0 Danco Financial Services, LLC 1 100.0 SYNCHRONY FINANCIAL 889 0.0 Statewide Credit Services Corp. 3 0.0 SUNRISE CREDIT SERVICES, INC 25 0.0 Caliber Home Loans, Inc. 8 0.0 Oportun Financial Corporation 11 0.0 MST Financial Services, L.L.C. 1 0.0 NATIONWIDE ADVANTAGE MORTGAGE COMPANY 2 0.0 Credit Associates of Maui, LTD 1 0.0 Alliance Data Card Services 373 0.0 FAIR COLLECTIONS & OUTSOURCING, INC. 30 0.0 TMAGNUSONE Inc 1 100.0 CCB Credit Serivces, Inc 3 0.0 Immediate Credit Recovery 1 0.0 ERNST, ARTMANN AND ASSOCIATES, INC. 1 0.0 Weltman, Weinberg & Reis Co., L.P.A. 3 0.0 Remex, Inc. 2 0.0 Go Capital Holdings, LLC 5 0.0 Tribal Lending Enterprise, Inc. 2 0.0 STONELEIGH RECOVERY ASSOCIATES, LLC 1 0.0 DRIVEiT Holdings, Inc. 1 0.0 BANK OF AMERICA, NATIONAL ASSOCIATION 638 0.16 Adler Wallach & Associates, Inc. 14 0.0 College Loan Corporation 1 0.0 Security Credit Services, LLC 29 3.45 Federal Adjustment Bureau, Inc. 4 0.0 Army and Air Force Exchange Service 21 19.05 Financial Credit Network Inc 5 0.0 Earnest Inc. 1 0.0 Medical Financial Services, Inc. 3 0.0 Dovenmuehle Mortgage, Inc. 1 0.0 ACCOUNTS ADVOCATE AGENCY 1 100.0 Eastern Revenue, Inc. 3 0.0 Early Warning Services, LLC 166 0.0 CMRE Financial Services, Inc. 22 9.09 Collections Acquisition Company, Inc. 5 20.0 Harvard Collections, LLC 10 0.0 Ideal Collection Services, Inc. 2 0.0 Accounts Receivable Inc. 7 0.0 COLLECTIONS UNLIMITED OF TEXAS INC 1 0.0 Federal Financial Services Inc 1 0.0 Central Portfolio Control Inc. 1 0.0 Pinnacle Financial Group, Inc. 2 50.0 Professional Credit Analysts of MN, Inc. 2 0.0 Overton, Russell, Doerr and Donovan, LLP 1 0.0 Summit Financial Corp. 2 100.0 CITIBANK, N.A. 850 0.0 PRESTIGE FINANCIAL SERVICES INC 12 0.0 TMX Finance LLC 1 0.0 Nationwide Financial Group 1 100.0 Dyck-O'Neal, Inc. 1 0.0 Law Offices of Timothy E. Baxter & Associates, P.C. 1 0.0 Allied Collection Services, Inc. (Nevada) 10 10.0 DeWitt Mortgage Services and Property Management, LLC 1 100.0 Baxter Bailey & Associates 1 100.0 Summit Collection Services, Inc. 1 0.0 LoanHero, Inc 1 100.0 Skrill USA, Inc. 1 0.0 Self Lender Inc 7 28.57 Experian Information Solutions Inc. 75599 0.0 CNG HOLDINGS INC 11 9.09 TFC Credit Corporation of California 3 66.67 Auto Trakk, LLC 5 0.0 LDF Holdings, LLC 2 0.0 RENASANT CORPORATION 1 0.0 Nationwide Credit Corporation 1 0.0 National Credit Systems,Inc. 132 1.52 Heritage Financial Group, Inc. 1 0.0 Darnel Quick Recovery, Inc. 1 0.0 Carvana Group, L

###### How can we look further?
- Using web crawler, check the user amount of this company. 
- Checking the narrative, generating words cloud to see.
- From time aspect, check whether these issued have been fixed. 

These top 3 companies all have timely response, so this time let's only focus on the amount about this issue during these years. 
The line chart shows, from 2015 by now, this issue has been increased gradually instead of improved. Since 2020, the complaints amount increased greatly.

In [0]:
df_company_improve = sqlContext.sql("SELECT company,date_received,to_timestamp(date_received, 'yyyy-MM') as received_ym," + \
                           " count(1) as total "         
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " AND sub_product='Credit reporting' " +\
                           " AND issue='Incorrect information on your report' AND sub_issue='Information belongs to someone else' "\
                           " AND ((company='TRANSUNION INTERMEDIATE HOLDINGS, INC.')  "
                           " OR (company='Experian Information Solutions Inc.')  "
                           " OR (company='EQUIFAX, INC.'))  "
                           " GROUP BY company,date_received,to_timestamp(date_received, 'yyyy-MM')")

display(df_company_improve)

company date_received received_ym total EQUIFAX, INC. 2019-01-25 2019-01-01T00:00:00.000+0000 25 EQUIFAX, INC. 2018-11-05 2018-11-01T00:00:00.000+0000 32 Experian Information Solutions Inc. 2018-11-08 2018-11-01T00:00:00.000+0000 32 EQUIFAX, INC. 2020-10-11 2020-10-01T00:00:00.000+0000 72 Experian Information Solutions Inc. 2020-12-16 2020-12-01T00:00:00.000+0000 217 EQUIFAX, INC. 2020-12-08 2020-12-01T00:00:00.000+0000 203 EQUIFAX, INC. 2020-10-28 2020-10-01T00:00:00.000+0000 145 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2020-01-27 2020-01-01T00:00:00.000+0000 100 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-11-14 2019-11-01T00:00:00.000+0000 78 EQUIFAX, INC. 2019-10-27 2019-10-01T00:00:00.000+0000 36 Experian Information Solutions Inc. 2020-06-07 2020-06-01T00:00:00.000+0000 50 Experian Information Solutions Inc. 2020-09-25 2020-09-01T00:00:00.000+0000 148 EQUIFAX, INC. 2020-05-23 2020-05-01T00:00:00.000+0000 57 EQUIFAX, INC. 2020-07-23 2020-07-01T00:00:00.000+0000 139 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2020-12-17 2020-12-01T00:00:00.000+0000 263 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2021-01-08 2021-01-01T00:00:00.000+0000 244 EQUIFAX, INC. 2020-08-21 2020-08-01T00:00:00.000+0000 87 Experian Information Solutions Inc. 2017-10-02 2017-10-01T00:00:00.000+0000 29 EQUIFAX, INC. 2017-09-05 2017-09-01T00:00:00.000+0000 9 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2017-09-03 2017-09-01T00:00:00.000+0000 3 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2017-11-25 2017-11-01T00:00:00.000+0000 4 EQUIFAX, INC. 2017-11-30 2017-11-01T00:00:00.000+0000 16 Experian Information Solutions Inc. 2017-11-19 2017-11-01T00:00:00.000+0000 5 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-01-19 2019-01-01T00:00:00.000+0000 11 Experian Information Solutions Inc. 2017-05-11 2017-05-01T00:00:00.000+0000 6 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2018-06-11 2018-06-01T00:00:00.000+0000 43 Experian Information Solutions Inc. 2018-08-11 2018-08-01T00:00:00.000+0000 14 Experian Information Solutions Inc. 2019-03-23 2019-03-01T00:00:00.000+0000 18 EQUIFAX, INC. 2018-11-25 2018-11-01T00:00:00.000+0000 17 EQUIFAX, INC. 2019-03-26 2019-03-01T00:00:00.000+0000 44 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-09-11 2019-09-01T00:00:00.000+0000 64 EQUIFAX, INC. 2019-06-10 2019-06-01T00:00:00.000+0000 50 EQUIFAX, INC. 2018-06-05 2018-06-01T00:00:00.000+0000 29 EQUIFAX, INC. 2020-07-21 2020-07-01T00:00:00.000+0000 119 EQUIFAX, INC. 2017-06-22 2017-06-01T00:00:00.000+0000 26 Experian Information Solutions Inc. 2020-06-26 2020-06-01T00:00:00.000+0000 127 EQUIFAX, INC. 2020-06-04 2020-06-01T00:00:00.000+0000 184 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2017-05-02 2017-05-01T00:00:00.000+0000 17 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2020-06-04 2020-06-01T00:00:00.000+0000 203 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2020-12-05 2020-12-01T00:00:00.000+0000 155 EQUIFAX, INC. 2017-07-18 2017-07-01T00:00:00.000+0000 19 Experian Information Solutions Inc. 2018-04-02 2018-04-01T00:00:00.000+0000 21 Experian Information Solutions Inc. 2018-08-28 2018-08-01T00:00:00.000+0000 34 EQUIFAX, INC. 2017-06-17 2017-06-01T00:00:00.000+0000 6 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2017-10-30 2017-10-01T00:00:00.000+0000 16 Experian Information Solutions Inc. 2017-11-01 2017-11-01T00:00:00.000+0000 12 EQUIFAX, INC. 2018-02-17 2018-02-01T00:00:00.000+0000 8 EQUIFAX, INC. 2018-05-30 2018-05-01T00:00:00.000+0000 22 Experian Information Solutions Inc. 2018-05-28 2018-05-01T00:00:00.000+0000 16 Experian Information Solutions Inc. 2018-05-30 2018-05-01T00:00:00.000+0000 25 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-11-23 2019-11-01T00:00:00.000+0000 43 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-05-20 2019-05-01T00:00:00.000+0000 45 TRANSUNION INTERMEDIATE HOLDINGS, INC. 2019-05-18 2019-05-01T00:00:00.000+0000 32 EQUIFAX, INC. 2019-02-19 2019-02-01T00:00:00.000+0000 40 EQUIFAX, INC. 2019-08-25 2019-08-01T00:00:00.000+0000 21 Experian Information Solutions Inc. 2018-08-07 2018-08-01T00:00:00.000+0000 33 TRANSUNION

#### By taking some sampling data, we have seen what the data looks like.
- **complaint_what_happened** is the description of what that consumer complained. By applying nlp related analysis, can we find the sentiment of these records. This is all about complaints, but there usually exists different levels of severity. If we can analysis these levels, it might be used for the future classification.
- Check the columns which have these standard items
- **date_received** and **date_sent_to_company** for applying time series analysis

| Column Name               | Remark   |
|-------------------------|----------|
| company                   | any change or converge|
| company_public_response   | is it standard?|
| company_response          | standard item|
| complaint_id              | primary key  |
| complaint_what_happened   | story|
| consumer_consent_provided | standard item|
| consumer_disputed         | standard item|
| date_received             | date yyyy-mm-dd|
| date_sent_to_company      | date yyyy-mm-dd|
| issue                     | standard item|
| product                   | standard item|
| state                     | CA|
| sub_issue                 | standard item|
| sub_product               | standard item|
| submitted_via             | standard item|
| tags                      | ?|
| timely                    | standard item|
| zip_code                  | is it standard?|

In [0]:
df.count()

#### Load dataset from csv file
- read data from the csv file, the first row as the header, and display
- observe the sample data

参考 https://cloud.tencent.com/developer/article/1096712

In [0]:
#view few lines
#csvFile.take(3)
#read header
header = csvFile.first()
#columns
fields = [StructField(field_name, StringType(), True) for field_name in header.split(',')]
#column count
len(fields)

Out[137]: 18

#### Process data schema 
- rename column names to make it easier to access
- normalize fieldcolumn data type
(reference https://www.nodalpoint.com/spark-data-frames-from-csv-files-handling-headers-column-types/   20210208)

In [0]:
#list the original fields, and modify them to correct data type
#fields
fields[0].dataType = TimestampType() #Date received
fields[12].dataType = TimestampType() #Date sent to company
#rename column names: replace minus to underscore, remove question, to lower case
for f in fields:
 f.name = f.name.replace(' ','_').replace('-','_').replace('?','').lower()
#construct a new schema
schema = StructType(fields) 

Out[148]: [StructField(date_received,TimestampType,true),
 StructField(product,StringType,true),
 StructField(sub_product,StringType,true),
 StructField(issue,StringType,true),
 StructField(sub_issue,StringType,true),
 StructField(consumer_complaint_narrative,StringType,true),
 StructField(company_public_response,StringType,true),
 StructField(company,StringType,true),
 StructField(state,StringType,true),
 StructField(zip_code,StringType,true),
 StructField(tags,StringType,true),
 StructField(consumer_consent_provided,StringType,true),
 StructField(submitted_via,TimestampType,true),
 StructField(date_sent_to_company,StringType,true),
 StructField(company_response_to_consumer,StringType,true),
 StructField(timely_response,StringType,true),
 StructField(consumer_disputed,StringType,true),
 StructField(complaint_id,StringType,true)]

In [0]:
'''
from pyspark.sql import SQLContext
from pyspark import SparkContext
sc =SparkContext()
sqlContext = SQLContext(sc)
'''
#observe the raw data from csv file to make sure applying the correct csv format
for line,item in zip(open('/tmp/complaints.csv','r').readlines(), range(3)):
    print(line)
#data = sqlContext.read.format('com.databricks.spark.csv').options(header='true', 
#inferschema='true').load('/FileStore/tables/complaints.csv')

--------------------------------------------------------------------------- 
 FileNotFoundError Traceback (most recent call last)
 <command-223265569878917> in <module> 
 6 '''
 7 #observe the raw data from csv file to make sure applying the correct csv format 
 ----> 8 for line , item in zip ( open ( '/tmp/complaints.csv' , 'r' ) . readlines ( ) , range ( 3 ) ) : 
 9 print ( line ) 
 10 #data = sqlContext.read.format('com.databricks.spark.csv').options(header='true', 

 FileNotFoundError : [Errno 2] No such file or directory: '/tmp/complaints.csv'

#### From the above lines, we can see 
- data field seperated by comma
- **Consumer complaint narrative** column is enclosed in double quotes.

In [0]:
display(data)

Date received Product Sub-product Issue Sub-issue Consumer complaint narrative Company public response Company State ZIP code Tags Consumer consent provided? Submitted via Date sent to company Company response to consumer Timely response? Consumer disputed? Complaint ID 2019-09-24 Debt collection I do not know Attempts to collect debt not owed Debt is not yours transworld systems inc. 
 null null null null null null null null null null null null is trying to collect a debt that is not mine not owed and is inaccurate." null TRANSWORLD SYSTEMS INC FL 335XX null Consent provided Web 2019-09-24 Closed with explanation Yes N/A 3384392 null null null null 2019-09-19 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Incorrect information on your report Information belongs to someone else null Company has responded to the consumer and the CFPB and chooses not to provide a public response Experian Information Solutions Inc. PA 15206 null Consent not provided Web 2019-09-20 Closed with non-monetary relief Yes N/A 3379500 2019-11-08 Debt collection I do not know Communication tactics Frequent or repeated calls Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. null Diversified Consultants, Inc. NC 275XX null Consent provided Web 2019-11-08 Closed with explanation Yes N/A 3433198 2019-09-15 Debt collection Other debt Attempts to collect debt not owed Debt was result of identity theft Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. null Pioneer Capital Solutions Inc CA 925XX null Consent provided Web 2019-09-15 Closed with explanation Yes N/A 3374555 2021-01-11 Payday loan, title loan, or personal loan Installment loan Charged fees or interest you didn't expect null null Company disputes the facts presented in the complaint Express Collections, Inc. MI 48114 null null Web 2021-01-11 Closed with explanation Yes N/A 4061634 2019-07-18 Mortgage Conventional home mortgage Closing on a mortgage null I started the process to refinance my current mortgage. The closing lawyer attempted to obtain the payoff statement, but they would not provide that statement for 4 business as they claimed they are behind. The lawyer informed me I could obtain the information sooner. I called and spoke to a representative on XX/XX/XXXX who said she could request I receive the payoff statement in 24 hours if she requested an expedite through a supervisor. I called back on XX/XX/XXXX, my closing date on the refinance, to determine the payoff amount as I had not yet received the payoff statement. I was told that it had not yet been generated, but still could be done today. I asked to speak to a supervisor and was told that one was not available and could call me within 24 hours. They also told me that there was no one within the company that could help me with this inquiry. Company has responded t

In [0]:
# Read dataset.Some descriptive column consist of quotation
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, DoubleType, TimestampType
df = (sqlContext.read.format("csv").
  option("header", "true").
  option("nullValue", "NA").
  option("inferSchema", True).
  option("delimiter",",").option("quote",'').option("escape",'').
  load("/FileStore/tables/complaints.csv"))
display(df)

Date received Product Sub-product Issue Sub-issue Consumer complaint narrative Company public response Company State ZIP code Tags Consumer consent provided? Submitted via Date sent to company Company response to consumer Timely response? Consumer disputed? Complaint ID 2019-09-24 Debt collection I do not know Attempts to collect debt not owed Debt is not yours "transworld systems inc. null null null null null null null null null null null null is trying to collect a debt that is not mine not owed and is inaccurate." null TRANSWORLD SYSTEMS INC FL 335XX null Consent provided Web 2019-09-24 Closed with explanation Yes N/A 3384392 null null null null 2019-09-19 "Credit reporting credit repair services or other personal consumer reports" Credit reporting Incorrect information on your report Information belongs to someone else null Company has responded to the consumer and the CFPB and chooses not to provide a public response Experian Information Solutions Inc. PA 15206 null Consent not provided Web 2019-09-20 Closed with non-monetary relief Yes 2019-11-08 Debt collection I do not know Communication tactics Frequent or repeated calls "Over the past 2 weeks I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work." null "Diversified Consultants Inc." NC 275XX null Consent provided Web 2019-11-08 Closed with explanation Yes 2019-09-15 Debt collection Other debt Attempts to collect debt not owed Debt was result of identity theft "Pioneer has committed several federal violations against me a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties." null Pioneer Capital Solutions Inc CA 925XX null Consent provided Web 2019-09-15 2021-01-11 "Payday loan title loan or personal loan" Installment loan Charged fees or interest you didn't expect null null Company disputes the facts presented in the complaint "Express Collections Inc." MI 48114 null null Web 2021-01-11 Closed with explanation 2019-07-18 Mortgage Conventional home mortgage Closing on a mortgage "" "I started the process to refinance my current mortgage. The closing lawyer attempted to obtain the payoff statement but they would not provide that statement for 4 business as they claimed they are behind. The lawyer informed me I could obtain the information sooner. I called and spoke to a representative on XX/XX/XXXX who said she could request I receive the payoff statement in 24 hours if she requested an expedite through a supervisor. I called back on XX/XX/XXXX my closing date on the refinance to determine the payoff amount as I had not yet received the payoff statement. I was told that it had not yet been generated but still could be done today. I asked to speak to a supervisor and was told that one was not available and could call me within 24 hours. They also told me that there was no one within the company that could help me with this inquiry." Company has responded to the consumer and the CFPB and chooses not to provide a public response Freedom Mor

####Check above sample dataset
- data loaded into wrong columns

In [0]:
csv = spark.read.csv('/FileStore/tables/complaints.csv', inferSchema=True, header=True)
#csv.show(10)
display(csv)

Date received Product Sub-product Issue Sub-issue Consumer complaint narrative Company public response Company State ZIP code Tags Consumer consent provided? Submitted via Date sent to company Company response to consumer Timely response? Consumer disputed? Complaint ID 2019-09-24 Debt collection I do not know Attempts to collect debt not owed Debt is not yours transworld systems inc. 
 null null null null null null null null null null null null is trying to collect a debt that is not mine not owed and is inaccurate." null TRANSWORLD SYSTEMS INC FL 335XX null Consent provided Web 2019-09-24 Closed with explanation Yes N/A 3384392 null null null null 2019-09-19 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Incorrect information on your report Information belongs to someone else null Company has responded to the consumer and the CFPB and chooses not to provide a public response Experian Information Solutions Inc. PA 15206 null Consent not provided Web 2019-09-20 Closed with non-monetary relief Yes N/A 3379500 2019-11-08 Debt collection I do not know Communication tactics Frequent or repeated calls Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. null Diversified Consultants, Inc. NC 275XX null Consent provided Web 2019-11-08 Closed with explanation Yes N/A 3433198 2019-09-15 Debt collection Other debt Attempts to collect debt not owed Debt was result of identity theft Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. null Pioneer Capital Solutions Inc CA 925XX null Consent provided Web 2019-09-15 Closed with explanation Yes N/A 3374555 2021-01-11 Payday loan, title loan, or personal loan Installment loan Charged fees or interest you didn't expect null null Company disputes the facts presented in the complaint Express Collections, Inc. MI 48114 null null Web 2021-01-11 Closed with explanation Yes N/A 4061634 2019-07-18 Mortgage Conventional home mortgage Closing on a mortgage null I started the process to refinance my current mortgage. The closing lawyer attempted to obtain the payoff statement, but they would not provide that statement for 4 business as they claimed they are behind. The lawyer informed me I could obtain the information sooner. I called and spoke to a representative on XX/XX/XXXX who said she could request I receive the payoff statement in 24 hours if she requested an expedite through a supervisor. I called back on XX/XX/XXXX, my closing date on the refinance, to determine the payoff amount as I had not yet received the payoff statement. I was told that it had not yet been generated, but still could be done today. I asked to speak to a supervisor and was told that one was not available and could call me within 24 hours. They also told me that there was no one within the company that could help me with this inquiry. Company has responded t

In [0]:
#show sample data
df.select(['Product','Complaint ID','Consumer complaint narrative']).show(20)
#data = csv.select("Product", "Complaint ID").where(col("Complaint ID").isNull())
#data.show(20)

#df2 = df.dropna(thresh=2,subset=('Product','Complaint ID'))
#df2.where(col("Complaint ID").isNull()).show(20)
#save to table1
sqlContext.registerDataFrameAsTable(df, "table1")

+--------------------+------------+----------------------------+
 Product|Complaint ID|Consumer complaint narrative|
+--------------------+------------+----------------------------+
 Debt collection| null| transworld system...|
 not owed and is ...| null| 335XX|
Credit reporting,...| 3379500| null|
 Debt collection| 3433198| Over the past 2 w...|
 Debt collection| 3374555| Pioneer has commi...|
Payday loan, titl...| 4061634| null|
 Mortgage| 3311105| I started the pro...|
Credit reporting,...| 4039920| null|
Credit reporting,...| null| "Previously, on X...|
Credit reporting,...| null| Hello This compla...|
 null| null| null|
 null| null| null|
 It states that t...| null| null|
 XXXX and Trans u...| null| NY|
Credit reporting,...| 3416481| null|
Credit card or pr...| 3446074| null|
 Debt collection| 4033158| null|
Credit reporting,...| 3446975| Today XX/XX/XXXX ...|
Credit reporting,...| 3379614| null|
Credit reporting,...| 3214857| XXXX is reporting...|
+--------------------+------------+----------------------------+
only showing top 20 rows

In [0]:
dfProduct = sqlContext.sql("SELECT `Complaint ID` as id,lower(Product) AS product, `Consumer complaint narrative` AS narrative " + \
                           ",`Submitted via` AS via FROM table1 ")
dfProduct = dfProduct.dropna()
#df2 = csv.na.drop()
#df.printSchema()


###import and download NLP related files

In [0]:
#!/bin/bash
!pip install nltk
!pip install --upgrade pip
!nltk.downloader all

In [0]:
import nltk
nltk.download('punkt')
nltk.download('twitter_samples')
nltk.download('averaged_perceptron_tagger')
nltk.download('maxent_ne_chunker')
nltk.download('words')
nltk.download('ieer')
nltk.download('stopwords')
#stopwords = set(STOPWORDS) 
stopwords = nltk.corpus.stopwords.words('english')


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data] Package punkt is already up-to-date!
[nltk_data] Downloading package twitter_samples to /root/nltk_data...
[nltk_data] Package twitter_samples is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data] /root/nltk_data...
[nltk_data] Package averaged_perceptron_tagger is already up-to-
[nltk_data] date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data] /root/nltk_data...
[nltk_data] Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to /root/nltk_data...
[nltk_data] Package words is already up-to-date!
[nltk_data] Downloading package ieer to /root/nltk_data...
[nltk_data] Package ieer is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data] Package stopwords is already up-to-date!

- Clearing text from punctuation (regexp_replace)
 - Tokenization (Tokenizer)
 - Delete stop words (StopWordsRemover)
 - Stematization (SnowballStemmer)
 - Filtering short words (udf)

### sample code

In [0]:
from pyspark.ml.feature import Tokenizer, RegexTokenizer
from pyspark.sql.functions import col, udf
from pyspark.sql.types import IntegerType

sentenceDataFrame = spark.createDataFrame([
    (0, "Hi I heard about Spark"),
    (1, "I wish Java could use case classes"),
    (2, "Logistic,regression,models,are,neat")
], ["id", "sentence"])

tokenizer = Tokenizer(inputCol="sentence", outputCol="words")

regexTokenizer = RegexTokenizer(inputCol="sentence", outputCol="words", pattern="\\W")
# alternatively, pattern="\\w+", gaps(False)

countTokens = udf(lambda words: len(words), IntegerType())

tokenized = tokenizer.transform(sentenceDataFrame)
tokenized.select("sentence", "words")\
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)

regexTokenized = regexTokenizer.transform(sentenceDataFrame)
regexTokenized.select("sentence", "words") \
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)

+-----------------------------------+------------------------------------------+------+
sentence |words |tokens|
+-----------------------------------+------------------------------------------+------+
Hi I heard about Spark |[hi, i, heard, about, spark] |5 |
I wish Java could use case classes |[i, wish, java, could, use, case, classes]|7 |
Logistic,regression,models,are,neat|[logistic,regression,models,are,neat] |1 |
+-----------------------------------+------------------------------------------+------+

+-----------------------------------+------------------------------------------+------+
sentence |words |tokens|
+-----------------------------------+------------------------------------------+------+
Hi I heard about Spark |[hi, i, heard, about, spark] |5 |
I wish Java could use case classes |[i, wish, java, could, use, case, classes]|7 |
Logistic,regression,models,are,neat|[logistic, regression, models, are, neat] |5 |
+-----------------------------------+------------------------------------------+------+

In [0]:
#get 100 sample data and remove id is null. backwords execution
dfProduct100 = dfProduct.dropna().limit(100)
type(dfProduct100)

Out[32]: pyspark.sql.dataframe.DataFrame

In [0]:
from pyspark.ml.feature import Tokenizer, RegexTokenizer
from pyspark.sql.functions import col, udf
from pyspark.sql.types import IntegerType

sentenceDataFrame = dfProduct100

regexTokenizer = RegexTokenizer(inputCol="product", outputCol="words", pattern="\\W")
countTokens = udf(lambda words: len(words), IntegerType())

regexTokenized = regexTokenizer.transform(sentenceDataFrame)
regexTokenized.select("product", "words") \
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)


+----------------------------------------------------------------------------+-------------------------------------------------------------------------------------+------+
product |words |tokens|
+----------------------------------------------------------------------------+-------------------------------------------------------------------------------------+------+
debt collection |[debt, collection] |2 |
debt collection |[debt, collection] |2 |
mortgage |[mortgage] |1 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit card or prepaid card |[credit, card, or, prepaid, card] |5 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
 or not applying for credit recently |[or, not, applying, for, credit, recently] |6 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
credit reporting, credit repair services, or other personal consumer reports|[credit, reporting, credit, repair, services, or, other, personal, consumer, reports]|10 |
+----------------------------------------------------------------------------+-------------------------------------------------------------------------------------+------+
only showing top 20 rows

In [0]:
#regexTokenized = regexTokenized.withColumn('words', concat_ws(' ', 'words'))
#regexTokenized.show(11)

In [0]:
#convert list column 'words' to string
#from pyspark.sql.functions import col, concat_ws
#words_list = regexTokenized.limit(100).select('words').collect() 
#stringList = ' '.join([str(item[0]) for item in words_list ])
#stringList
#import pyspark.sql.functions.*
#dfTokenized.select(concat_ws(' ', split(dfTokenized.words)).alias('content')).collect()

In [0]:
#word cloud
!pip install wordcloud
from wordcloud import WordCloud 
from wordcloud import WordCloud, STOPWORDS 
import matplotlib.pyplot as plt 

In [0]:
#stopwords = set(STOPWORDS) 
comment_words = ''  
# iterate through the csv file 
#for val in regexTokenized.words: 
    # typecaste each val to string 
    # split the value 
    ##tokens = val.split() 
    # Converts each token into lowercase 
    ##for i in range(len(tokens)): 
    ##    tokens[i] = tokens[i].lower() 
      
    ##comment_words += " ".join(tokens)+" "
#    comment_words += " ".join(val)+" "
wordcloud = WordCloud(width = 800, height = 800, 
                background_color ='white', 
                min_font_size = 10).generate('credit reporting credit repair services or other personal consumer reports debt collection debt collection payday loan title loan or personal loan mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit card or prepaid card debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit card or prepaid card credit reporting credit repair services or other personal consumer reports vehicle loan or lease credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports checking or savings account debt collection credit reporting credit repair services or other personal consumer reports checking or savings account credit reporting credit repair services or other personal consumer reports mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports or not applying for credit recently credit card or prepaid card debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services') 


In [0]:
  
# plot the WordCloud image                        
plt.figure(figsize = (8, 8), facecolor = None) 
plt.imshow(wordcloud) 
plt.axis("off") 
plt.tight_layout(pad = 0) 
plt.show() 

###NLP
-  DocumentAssembler(), one of the most essential transformers of the Spark NLP library. It’s the entry point to get your data in, and then process further with annotators. And, without linking its output to annotators in a pipeline, it has no meaning. In the following articles, we will talk about how you can apply certain NLP tasks on top of DocumentAssembler()

In [0]:
from sparknlp.base import *
documentAssembler = DocumentAssembler().setInputCol("product").setOutputCol("document").setCleanupMode("shrink")
doc_df = documentAssembler.transform(dfProduct100)
doc_df.show(10)

--------------------------------------------------------------------------- 
 ModuleNotFoundError Traceback (most recent call last)
 <command-1408914092487596> in <module> 
 ----> 1 from sparknlp . base import * 
 2 documentAssembler = DocumentAssembler ( ) . setInputCol ( "product" ) . setOutputCol ( "document" ) . setCleanupMode ( "shrink" ) 
 3 doc_df = documentAssembler . transform ( dfProduct100 ) 
 4 doc_df . show ( 10 ) 

 ModuleNotFoundError : No module named 'sparknlp'

####flatten the document column

In [0]:
doc_df.select("document.result").take(1)
import pyspark.sql.functions as F
doc_df.withColumn("tmp",F.explode("document")).select("tmp.*").show(3)

In [0]:
wordcloud = WordCloud(width = 800, height = 800, 
                background_color ='white', 
                stopwords = stopwords, 
                min_font_size = 10).generate(stringList) 
  
# plot the WordCloud image                        
plt.figure(figsize = (8, 8), facecolor = None) 
plt.imshow(wordcloud) 
plt.axis("off") 
plt.tight_layout(pad = 0) 
plt.show() 

In [0]:
dfNarrative = dfProduct.filter("narrative IS NOT NULL")
dfNarrative.show(3)
#dfNarrative = dfProduct.select("narrative", "id").where(col("narrative").isNoNull())
#dfNarrative.show(20)

+-------+---------------+--------------------+
 id| product| narrative|
+-------+---------------+--------------------+
3433198|debt collection|Over the past 2 w...|
3374555|debt collection|Pioneer has commi...|
3311105| mortgage|I started the pro...|
+-------+---------------+--------------------+
only showing top 3 rows

In [0]:
dfNarrative.count()

Out[63]: 455942

#### Where are these customers, in which way they complained.
 - using geo information to visualize the distribution of these consumers.
 - count the complaint record by source.

In [0]:
display(dfProduct)

id product narrative via 3433198 debt collection Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. Web 3374555 debt collection Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. Web 3311105 mortgage I started the process to refinance my current mortgage. The closing lawyer attempted to obtain the payoff statement, but they would not provide that statement for 4 business as they claimed they are behind. The lawyer informed me I could obtain the information sooner. I called and spoke to a representative on XX/XX/XXXX who said she could request I receive the payoff statement in 24 hours if she requested an expedite through a supervisor. I called back on XX/XX/XXXX, my closing date on the refinance, to determine the payoff amount as I had not yet received the payoff statement. I was told that it had not yet been generated, but still could be done today. I asked to speak to a supervisor and was told that one was not available and could call me within 24 hours. They also told me that there was no one within the company that could help me with this inquiry. Web 3446975 credit reporting, credit repair services, or other personal consumer reports Today XX/XX/XXXX went online to dispute the incorrect personal information and it says This request can not be processed online Web 3214857 credit reporting, credit repair services, or other personal consumer reports XXXX is reporting incorrectly to Equifax and XXXX an account balance of {$2300.00} on the XXXX partial account number XXXX. ( Please see pages 12 and 13 of the attached credit report ). This account is over 7 years old and therefore should not be on my credit report. This incorrect reporting is harming my credit score and is a Fair Credit Reporting Act ( F.C.R.A. ) violation. Web 3417374 credit reporting, credit repair services, or other personal consumer reports Please reverse the late payments reported on the following accounts : XXXX XXXX XXXX XXXX XXXX XXXX XXXX The accounts were never past due, I never made a late payment to this company ever please change this, I have a good relationship with these companies. Web 3415907 credit reporting, credit repair services, or other personal consumer reports i am a victim of identity theft as previously stated Web 3158699 credit card or prepaid card I was shocked when I reviewed my credit report and found late payment on the date 60 days late as of XX/XX/2017 and XX/XX/2017. I am not sure how this happened, I believe that I had made my payments to you when I received my statements. My only thought is that my monthly statement did not get to me. Web 3444592 credit reporting, credit repair services, or other personal consumer reports I would like the credit bureau to correct my XXXX XXXX XXXX XXXX balance. My correct balance is XXXX Web 3448432 credit reporting, credit repair services, or other personal consumer 

In [0]:
#pie chart
#dfProduct.agg({'via': 'count'}).withColumnRenamed("count(via)", "via_count").show()
import pyspark.sql.functions as F
from pyspark.sql import Window
w = Window.partitionBy('via')
#dfProduct.groupBy('via').count().select('via', dfProduct.col('count').alias('via_count')).show(10)
#dfProduct.select('via', dfProduct.count('via').over(w).alias('via_count')).sort('via').show()

#dfProduct.withColumn('via', F.count('via').over(w)).sort('via').show()
dfVia = sqlContext.sql(\
                           "SELECT `Submitted via` AS via, " + \
                           "COUNT(`Submitted via`) OVER (PARTITION BY `Submitted via`) as via_count " + \
                           "FROM table1 ")
display(dfVia)
#dfProduct.groupBy(F.col('via')).agg(F.count('via').alias('via_count')).show()


via via_count XXXX advising we are still a month behind. I have since been in contact with the Chase Executive Offices and have been advised 1 Deceptive or Abusive Acts or Practices." 1 I got a message that said to go to the website and 1 I hung up. I called the executive team 1 I started to receive alerts thru Credit wise 1 LLC itself. 1 OH XXXX Thank You 1 OHXXXX XXXX 7 OHXXXX XXXX 7 OHXXXX XXXX 7 OHXXXX XXXX 7 OHXXXX XXXX 7 OHXXXX XXXX 7 OHXXXX XXXX 7 SIGNED AND DATED. ECT. REGARDING OUR REFINANCE CASH -OUT WE WILL PROVIDE THE DOCUMENTS. 1 Trustees discovered that the laws regarding Mortgage Assignments varied significantly from state to state. Many issues regarding such Assignments were simply unresolved. One of the most significant issues was whether Mortgage Assignments could be back-dated or have retroactive effective dates. This issue arose because Trustees and their lawyers discovered in the foreclosure process that the Assignments could not actually be located 1 XX/XX/XXXX and XX/XX/XXXX and was continually told I was not authorized to speak about her account even though I personally took acceptable documentation into a XXXX branch and it was visually inspected by the branch manager. I was finally told on XX/XX/XXXX that they considered me eligible to speak about her account 1 XXXX '' And remember 1 XXXX XXXX and that they had not received the original check. 1 admits that they know these companies do this kind of thing. That conversation is notated on the XX/XX/XXXX letter. 1 after requesting a quote I did not purchase a policy. To my surprise the following month my bill which is normally XXXX jumped to XXXX 1 alleging that the company called more than a hundred times to try and collect someone elses debt. The phone call lawsuit claims that Discovers actions violate federal laws detailed in the Telephone Consumer Protection Act ( TCPA ) designed to protect the public from harassment Law360 1 among other things. The check was enclosed 1 and I had to withdraw my offer and cancel the escrow. This feels like unfair practice and deceptive bargaining. I am only requesting that this "" Short-sale with multiple late 's! '' be removed from my Escrow investigation XXXX XXXX XXXX XXXX or any other Escrow tool now 1 and U.S. Bank is obligated to return my funds for the fraudulent check 1 and a thorough lack of communication the entire time." 1 and he says that they thought the check was supposed to be sent to the car rental company 1 and other companies that reported the identity theft-related information to the CRA ( furnishers ) are responsible for blocking fraudulent information from appearing in victims credit reports 1 and providing approval as the payee 1 and rent while being unemployed 1 and skipping the loan I had asked them not to.I did speak with a representative who acknowledged the issue with my account and is working to fix it. My concern 1 and the closes branch is XXXX miles away from my home. This is my first credit card and now i am unable to make my XXXX 's payment since my account was frozen and I do not live near a branch. I'm XXXX years old and recently lost my part-time job due to them closing because of COVID 19 1 and the customer service representative said it was! Again speaking in another phone call in XX/XX/XXXX where M & T 1 and the maximum transfer amount allowed was {$3500.00} 1 any additional information in email 1 because it is paid ) 1 both conditions for which I take medication. If someone can help or protect me from these vultures 1 but Equifax continued to deny that they ever received such information. 1 but I need to work to support myself. 1 but it never did. 1 but my sister and I were both required to sign after we turned XXXX. However 1 by adding one line of code that stops payments from being deducted on a "" current XXXX '' balance." 1 customer service. Although everyone was nice and mannerable and empathetic 1 dated XXXX/XXXX/XXXX. it 's not supposed to be removed off any of my credit r

In [0]:

dfTest = sqlContext.sql(\
                           "SELECT * FROM table1 WHERE `Complaint ID`='1471337'")
display(dfTest)

Date received Product Sub-product Issue Sub-issue Consumer complaint narrative Company public response Company State ZIP code Tags Consumer consent provided? Submitted via Date sent to company Company response to consumer Timely response? Consumer disputed? Complaint ID

In [0]:
dfProduct.select('via', F.count('via').over(w).alias('via_count')).show()

+--------------------+---------+
 via|via_count|
+--------------------+---------+
 XXXX advising ...| 1|
 I got a message ...| 1|
 I hung up. I cal...| 1|
 I started to rec...| 1|
 OH XXXX Thank You| 1|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 OHXXXX XXXX| 7|
 XX/XX/XXXX and X...| 1|
 after requesting...| 1|
 alleging that th...| 1|
 among other thin...| 1|
 and U.S. Bank is...| 1|
 and he says that...| 1|
 and providing ap...| 1|
 and skipping the...| 1|
+--------------------+---------+
only showing top 20 rows

In [0]:
display(dfProduct)

id product narrative 3433198 debt collection Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. 3374555 debt collection Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. 3311105 mortgage I started the process to refinance my current mortgage. The closing lawyer attempted to obtain the payoff statement, but they would not provide that statement for 4 business as they claimed they are behind. The lawyer informed me I could obtain the information sooner. I called and spoke to a representative on XX/XX/XXXX who said she could request I receive the payoff statement in 24 hours if she requested an expedite through a supervisor. I called back on XX/XX/XXXX, my closing date on the refinance, to determine the payoff amount as I had not yet received the payoff statement. I was told that it had not yet been generated, but still could be done today. I asked to speak to a supervisor and was told that one was not available and could call me within 24 hours. They also told me that there was no one within the company that could help me with this inquiry. 3446975 credit reporting, credit repair services, or other personal consumer reports Today XX/XX/XXXX went online to dispute the incorrect personal information and it says This request can not be processed online 3214857 credit reporting, credit repair services, or other personal consumer reports XXXX is reporting incorrectly to Equifax and XXXX an account balance of {$2300.00} on the XXXX partial account number XXXX. ( Please see pages 12 and 13 of the attached credit report ). This account is over 7 years old and therefore should not be on my credit report. This incorrect reporting is harming my credit score and is a Fair Credit Reporting Act ( F.C.R.A. ) violation. 3417374 credit reporting, credit repair services, or other personal consumer reports Please reverse the late payments reported on the following accounts : XXXX XXXX XXXX XXXX XXXX XXXX XXXX The accounts were never past due, I never made a late payment to this company ever please change this, I have a good relationship with these companies. 3415907 credit reporting, credit repair services, or other personal consumer reports i am a victim of identity theft as previously stated 3158699 credit card or prepaid card I was shocked when I reviewed my credit report and found late payment on the date 60 days late as of XX/XX/2017 and XX/XX/2017. I am not sure how this happened, I believe that I had made my payments to you when I received my statements. My only thought is that my monthly statement did not get to me. 3444592 credit reporting, credit repair services, or other personal consumer reports I would like the credit bureau to correct my XXXX XXXX XXXX XXXX balance. My correct balance is XXXX 3448432 credit reporting, credit repair services, or other personal consumer reports The credit bureaus are reporting

#### How many valid and invalid complaints within the dataset?

The government provides platforms for financial products